In [1]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from datasets import load_from_disk

<frozen importlib._bootstrap>:241: RuntimeWarning: pyarrow._fs.FileInfo size changed, may indicate binary incompatibility. Expected 64 from C header, got 88 from PyObject
<frozen importlib._bootstrap>:241: RuntimeWarning: pyarrow._fs.FileSelector size changed, may indicate binary incompatibility. Expected 48 from C header, got 72 from PyObject


In [2]:
keyword_generation_task_dataset = load_from_disk('../datasets/tasks/keyword_generation_task_dataset/')

In [3]:
keyword_generation_task_dataset = keyword_generation_task_dataset.map(lambda row: {'labels': row['text'].split(':')[-1].strip().split(', ')})

In [4]:
text = keyword_generation_task_dataset['test'][0]['text']

In [5]:
''.join(text.split(':')[:-1])

'[címkék generálása]\nBelföld Novemberre idézi be a bíró Gyurcsány Ferencet\n\nGyurcsány Ferencet és Jánosi Györgyöt november 12-ére, Szilvásy Györgyöt és Benedek Andrást november 16-ára, Mesterházy Attilát és Keszthelyi Andrást november 18-ára idézi be a Zuschlag-perben tanúkénti meghallgatásra a Bács-Kiskun Megyei Bíróság - közölte Fodor Endre tanácsvezető bíró a hétfői tárgyalási napon Kecskeméten.\n\nGyurcsány Ferencet és Jánosi Györgyöt november 12-ére, Szilvásy Györgyöt és Benedek Andrást november 16-ára, Mesterházy Attilát és Keszthelyi Andrást november 18-ára idézi be a Zuschlag-perben tanúkénti meghallgatásra a Bács-Kiskun Megyei Bíróság - közölte Fodor Endre tanácsvezető bíró a hétfői tárgyalási napon Kecskeméten.\nKözlése szerint a szeptemberben és októberben lefolytatott bizonyítási eljárás alapján ezeket a személyeket, akiknek vélhetően tudomásuk van a vád tárgyává tett cselekményről, legalábbis annak egy részéről, indokolt meghallgatni.\nGyurcsány Ferenc és Jánosi György 

In [6]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel, PeftConfig
from transformers import BitsAndBytesConfig
import torch

model_id = "mistralai/Mistral-7B-v0.1"
peft_model_id = '../finetune/qlora-out-keyword-extraction/'

config = PeftConfig.from_pretrained(peft_model_id)
model = AutoModelForCausalLM.from_pretrained(
    model_id,
    load_in_4bit=True,
    device_map='auto',
    torch_dtype=torch.bfloat16,
    quantization_config=BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=True,
        bnb_4bit_quant_type='nf4'
    ),
)
model = PeftModel.from_pretrained(model, peft_model_id)

tokenizer = AutoTokenizer.from_pretrained(model_id)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

CUDA extension not installed.
CUDA extension not installed.


In [7]:
from tqdm import tqdm

device = 'cuda:0'
preds = []
truths = []
for row in tqdm(keyword_generation_task_dataset['test']):
    text = row['text']
    labels = row['labels']
    input_text = ''.join(text.split(':')[:-1])+':'
    with torch.cuda.amp.autocast():
        inputs = tokenizer(input_text, return_tensors="pt").to(device)
        if len(inputs['input_ids'][0]) > 2048:
            continue
        outputs = model.generate(input_ids=inputs['input_ids'], max_new_tokens=40)
        result = tokenizer.decode(outputs[0], skip_special_tokens=True)
        sresult = result[result.rfind(':')+2:].strip()
        output_labels = sresult.strip().split(', ')
        truths.append(labels)
        preds.append(output_labels)

  0%|                                                                                                                                                    | 0/1710 [00:00<?, ?it/s]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
2023-11-27 19:02:15.039590: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-11-27 19:02:15.039725: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-11-27 19:02:15.042297: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register 

In [8]:
list(zip(preds, truths))

[(['csalás', 'támogatás'], ['támogatás']),
 (['bankok - pénzintézetek', 'brókerbotrány', 'külügyminisztérium', 'rokonok'],
  ['bankok - pénzintézetek', 'közigazgatás']),
 (['hivatali visszaélés',
   'ítélet/döntés',
   'önkormányzat',
   'sport',
   'vesztegetés'],
  ['jegyző',
   'önkormányzat',
   'protekció',
   'sport',
   'támogatás',
   'ügyészség',
   'vesztegetés']),
 (['állami/önkormányzati szerződések',
   'hirdetés',
   'klientúra',
   'közbeszerzés',
   'PR',
   'rokonok'],
  ['közbeszerzés']),
 (['juttatás', 'összeférhetetlenség', 'vagyonosodás / vagyonnyilatkozat'],
  ['vagyonosodás / vagyonnyilatkozat']),
 (['hirdetés', 'klientúra', 'média', 'pályázat'],
  ['állami/önkormányzati szerződések', 'média', 'pályázat']),
 (['állami / önkormányzati vállalat',
   'közbeszerzés',
   'közlekedés',
   'pályázat'],
  ['állami / önkormányzati vállalat',
   'EU',
   'közbeszerzés',
   'közlekedés',
   'lobbi',
   'támogatás',
   'vasút']),
 (['állami/önkormányzati szerződések', 'építő

In [9]:
all_possible_labels = set()
for labels in truths:
    for label in labels:
        all_possible_labels.add(label)
for labels in preds:
    for label in labels:
        all_possible_labels.add(label)
label_to_id = {key: value for value, key in enumerate(all_possible_labels)}
label_to_id

{'': 0,
 'munkaügy': 1,
 'környezetvé': 2,
 'napelem / megújulók': 3,
 'kultúra - művészet': 4,
 'közokirat-hamis': 5,
 'titkosszolg': 6,
 'dohányipar': 7,
 'közigazgatás': 8,
 'hamis vád': 9,
 'jogosulatlan gazdasági előny': 10,
 'tőzsde': 11,
 'hamis magánokirat felhasználása': 12,
 'mentelmi jog': 13,
 'vagy': 14,
 'őrzés-védés': 15,
 'bűnpártol': 16,
 'közérdekű adat': 17,
 'bennfentes kereskedelem': 18,
 'emberi jogok - egyéni szabadság': 19,
 'mulasztás': 20,
 'nyom': 21,
 'foglalkoztatás': 22,
 'műemlékvédelem': 23,
 'választások -': 24,
 '(igazságügyi) szakértő': 25,
 'hulladéküzlet': 26,
 'jegyző': 27,
 'magánokirat-hamisítás': 28,
 'bűnszervezet / bűnszövetség': 29,
 'hirdetés': 30,
 'OLAF-vizsgálat,': 31,
 'közlekedés': 32,
 'juttatás': 33,
 'környezetká': 34,
 'adatigénylés': 35,
 'atom': 36,
 'számviteli fegyelem me': 37,
 'ellenőrzés': 38,
 'nemzeti park': 39,
 'protekció': 40,
 'film': 41,
 'prémium': 42,
 'külügyminisztérium': 43,
 'jogalkotás': 44,
 'vizsgálóbizotts': 

In [10]:
i_preds = [[1 if value in preds_a else 0 for value in label_to_id] for preds_a in preds]

In [11]:
i_preds

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


In [12]:
i_truths = [[1 if value in truths_a else 0 for value in label_to_id] for truths_a in truths]

In [13]:
from sklearn.metrics import classification_report

print(classification_report(i_truths, i_preds, target_names=label_to_id))

                                             precision    recall  f1-score   support

                                                  0.85      0.74      0.79       129
                                   munkaügy       0.00      0.00      0.00         0
                                környezetvé       0.00      0.00      0.00         0
                        napelem / megújulók       0.00      0.00      0.00         3
                         kultúra - művészet       0.30      0.73      0.42        11
                            közokirat-hamis       0.00      0.00      0.00         0
                                titkosszolg       0.00      0.00      0.00         0
                                 dohányipar       0.33      0.50      0.40         4
                               közigazgatás       0.00      0.00      0.00        11
                                  hamis vád       0.00      0.00      0.00         1
               jogosulatlan gazdasági előny       0.00      0.00

/home/boa/.conda/envs/ai/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/boa/.conda/envs/ai/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [14]:
precision, recall, f1, _ = precision_recall_fscore_support(i_truths, i_preds)
acc = accuracy_score(labels, preds)
{
    'accuracy': acc,
    'precision': precision,
    'recall': recall,
    'f1': f1
}

/home/boa/.conda/envs/ai/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/boa/.conda/envs/ai/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ValueError: Found input variables with inconsistent numbers of samples: [1, 1178]

In [ ]:
import numpy as np
y_true = np.array([[0, 1, 1, 1],[0,0,1,0],[1,1,0,0]])
y_scores = np.array([[0.2, 0.6, 0.1, 0.8],[0.4,0.9,0.8,0.6],[0.8,0.4,0.5,0.7]])
threshold = 0.5
y_pred=[]
for sample in  y_scores:
  y_pred.append([1 if i>=0.5 else 0 for i in sample ] )
y_pred = np.array(y_pred)
y_pred


In [ ]:
from sklearn.metrics import accuracy_score
accuracy_score(i_truths, i_preds)


In [ ]:
print("Actual \n", y_true)
print("\nPredicted \n",y_pred)


In [ ]:
from sklearn.metrics import multilabel_confusion_matrix
multilabel_confusion_matrix(i_truths, i_preds)
